
# Carbon Black Reactor.

Simulate carbon black production, using the :py:class:`~bloc.reactors.CarbonBlackIdealGasConstPressureReactor`
class to predict the specific surface area of carbon.


In [ ]:
import cantera as ct
import matplotlib.pyplot as plt
from spy.misc.arrays import logspace

from bloc.reactors import CarbonBlackIdealGasConstPressureReactor
from bloc.utils import get_mechanism_path

mechanism = get_mechanism_path("Fincke_GRC.yaml")
composition = "CH4:1.0"

T_C = 1300  # °C
P_atm = 1  # atm

g = ct.Solution(mechanism)
g.TPX = T_C + 273.15, P_atm * ct.one_atm, composition
# Cantera units : T in K; P in Pa (converted from one_atm above)

reactor = CarbonBlackIdealGasConstPressureReactor(g, energy="off")
sim = ct.ReactorNet([reactor])

# Create a SolutionArray object to store the simulation results.
states = ct.SolutionArray(g, extra=["t", "specific_surface"])

# Run the simulation for different residence times
for t in logspace(0.001, 1, 50):  # s
    sim.advance(t)
    reactor.residence_time = t  # s
    print("Residence time: {:.2e} s".format(t))

    states.append(
        reactor.thermo.state, t=t, specific_surface=reactor.guess_specific_surface()
    )

-----------------------------------------------------------------------------



In [ ]:
plt.figure()
plt.plot(states.t, states.specific_surface, "--", lw=2, color="black", label="m2/g")
# set ymin to 0
plt.ylim(bottom=0)
plt.xlabel("Residence time (s)")
plt.ylabel("Specific surface (m2/g)")

# Plot CH4, C2H2 and C(s) mole fractions as a function of residence time on a secondary y-axis
plt.twinx()
plt.plot(states.t, states.Y[:, g.species_index("CH4")] * 100, "r-", label="CH4")
plt.plot(states.t, states.Y[:, g.species_index("C2H2")] * 100, "b-", label="C2H2")
plt.plot(
    states.t,
    states.Y[:, g.species_index("C(s)")] * 100,
    "-",
    color="black",
    label="C(s)",
)
plt.ylabel("Mass fraction (%)")
plt.legend()


plt.show()